In [1]:
import pandas as pd
import numpy as np
import pickle, warnings, datetime, gc, ctypes
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA, IncrementalPCA
warnings.filterwarnings('ignore')

In [2]:
def downcast(df, verbose = True):
    start_memory = df.memory_usage().sum() / 1024 ** 2
    for col in df.columns:
        dtype_name = df[col].dtype.name
        if dtype_name == "object" or 'date' in dtype_name:
            pass
        elif dtype_name == "bool":
            df[col] = df[col].astype("int8")
        elif dtype_name.startswith("int") or (df[col].round() == df[col]).all():
            df[col] = pd.to_numeric(df[col], downcast = "integer")
        else:
            df[col] = pd.to_numeric(df[col], downcast = "float")
    end_memory = df.memory_usage().sum() / 1024 ** 2

    if verbose:
        print("{:.1f}% compressed".format(100 * (start_memory - end_memory) / start_memory))

    return df

In [3]:
def subPCA(df, n, p):
    cols = df.columns.tolist()
    subset_size = int(np.ceil(len(cols) / n))
    pca_results = []
    pca_colnames = []

    for i in range(n):
        subset_cols = cols[i*subset_size:(i+1)*subset_size]
        if not subset_cols:
            continue
        subset = df[subset_cols]
        pca = PCA()
        subset_pca = pca.fit_transform(subset)
        cum_var = np.cumsum(pca.explained_variance_ratio_)
        n_components = np.argmax(cum_var >= p) + 1
        subset_pca = subset_pca[:, :n_components]
        pca_results.append(subset_pca)
        pca_colnames += [f'pca_sub{i+1}_{j+1:04d}' for j in range(n_components)]
        print(f"Processed subset {i+1}/{n} with {n_components} components.")

    combined = np.concatenate(pca_results, axis=1)
    return pd.DataFrame(combined, index=df.index, columns=pca_colnames)

In [4]:
with open('../../data/processed/gdelt_llm_sentiment.pkl', 'rb') as f:
    llm_data = pickle.load(f)
llm_data = downcast(llm_data, verbose = True)

0.0% compressed


In [5]:
# Determine which times to keep based on the stock data
with open(r"../../Data/Processed/stock_data_simple.pkl", 'rb') as f:
    stock_data = pickle.load(f)

stock_data['date'] = stock_data.index.date
days = list(stock_data['date'].unique())
stock_times = stock_data.index.unique().tolist()

In [6]:
with open(r'../../data/processed/gdelt_intermediate_cleaned.pkl', 'rb') as f:
    df = pickle.load(f)
df = downcast(df, verbose = True)

0.0% compressed


In [7]:
df.index = df['GKGRECORDID']
df.drop(columns=['GKGRECORDID'], inplace=True)

llm_data.index = llm_data['GKGRECORDID']
llm_data.drop(columns=['GKGRECORDID'], inplace=True)

In [8]:
# Perform initial PCA on LLM data
index = llm_data.index
pca = PCA()
pca_fit = pca.fit_transform(llm_data)
cum_var = np.cumsum(pca.explained_variance_ratio_)
n_components = np.argmax(cum_var >= 0.8) + 1
print(f"Number of components explaining at least 80% of the variance: {n_components}")
llm_data = pd.DataFrame(pca_fit[:,:n_components], index=index, columns=[f'llm_pca_{i+1:03d}' for i in range(n_components)])

Number of components explaining at least 80% of the variance: 120


In [9]:
# Renaming GDELT columns from airline name to stock ticker
df.columns = [col.replace('Allegiant Air', 'ALGT') for col in df.columns]
df.columns = [col.replace('Alaska Airlines', 'ALK') for col in df.columns]
df.columns = [col.replace('United Airlines', 'UAL') for col in df.columns]
df.columns = [col.replace('Delta Air Lines', 'DAL') for col in df.columns]
df.columns = [col.replace('JetBlue', 'JBLU') for col in df.columns]
df.columns = [col.replace('Southwest Airlines', 'LUV') for col in df.columns]
df.columns = [col.replace('American Airlines', 'AAL') for col in df.columns]

In [10]:
df.drop(columns=['airplane','airline','airport','Frontier Airlines','Hawaiian Airlines',
                 'Spirit Airlines','Sun Country Airlines','article_title','V2SOURCECOMMONNAME','V2DOCUMENTIDENTIFIER','V1THEMES'
                 ], inplace=True)

In [11]:
# Perform initial PCA on sentiment data
index = df.index
cols_to_pca = [i for i in df.columns if i not in ['datetime','date','ALK','AAL','DAL','JBLU','LUV','UAL','ALGT','Tone']]
df_to_pca = df[cols_to_pca]
df.drop(columns=cols_to_pca, inplace=True)
scaler = StandardScaler()
df_to_pca = scaler.fit_transform(df_to_pca)
pca = IncrementalPCA(batch_size=50000)
df_to_pca = pca.fit_transform(df_to_pca)
cum_var = np.cumsum(pca.explained_variance_ratio_)

In [12]:
n_components = np.argmax(cum_var >= 0.8) + 1
print(f"Number of components explaining at least 80% of the variance: {n_components}")
df_to_pca = pd.DataFrame(df_to_pca[:,:n_components], index=index, columns=[f'sentiment_pca_{i+1:03d}' for i in range(n_components)])
df = pd.concat([df, df_to_pca], axis=1)

Number of components explaining at least 80% of the variance: 142


In [13]:
df = pd.merge(df, llm_data, left_index=True, right_index=True, how='left')

In [14]:
# Create topic-specific metrics columns
df['Article Count'] = 1

topics  = ['AAL','ALGT','ALK','DAL','JBLU','LUV','UAL']
metrics = [i for i in df.columns if 'pca' in i or i in ['Article Count','Tone']]

for topic in topics:
    for metric in metrics:
        df[f'{topic}_{metric}'] = df[metric] * df[topic]

In [15]:
# Convert from UTC to EST, accounting for daylight saving time
df['datetime'] = pd.to_datetime(df['datetime'], utc=True)
df['datetime'] = df['datetime'].dt.tz_convert('America/New_York')

# Remove the timezone information 
df['datetime'] = df['datetime'].dt.tz_localize(None)

In [16]:
df['datetime'].describe()

count                          1121056
mean     2021-05-16 18:00:53.125446400
min                2017-12-31 19:15:00
25%                2019-04-10 18:15:00
50%                2021-01-29 12:30:00
75%                2023-07-24 21:30:00
max                2025-05-31 19:45:00
Name: datetime, dtype: object

In [17]:
# Create a grouped dataframe, grouped by datetime, that creates a sum for each metric
grouped_df = df.groupby('datetime').agg(
    {f'{topic}_{metric}': ['sum'] for topic in topics for metric in metrics}
)

# Flatten the MultiIndex columns
grouped_df.columns = ['_'.join(col).strip().replace('_sum','') for col in grouped_df.columns.values]

In [18]:
# Fill in all missing times
current_times = grouped_df.index.tolist()
to_add = list(set(stock_times) - set(current_times)) # fast way to figure out which stock times are missing
df_to_add = pd.DataFrame(index=to_add, columns=grouped_df.columns)
df_to_add = df_to_add.fillna(0)

grouped_df = pd.concat([grouped_df, df_to_add], copy=False, sort=True)

In [19]:
##### Handling after-hours articles #####
grouped_df['datetime'] = grouped_df.index
grouped_df['time'] = grouped_df['datetime'].dt.time
grouped_df['date'] = grouped_df['datetime'].dt.date

# Join with stock data
grouped_df['stock_time'] = np.where(grouped_df['date'].isin(days), grouped_df['datetime'], pd.NaT)
# Limit times after 15:45 and before 9:15
grouped_df['stock_time'] = np.where(grouped_df['time'] > datetime.time(15,45,0), pd.NaT, grouped_df['stock_time'])
grouped_df['stock_time'] = np.where(grouped_df['time'] < datetime.time(9,30,0) , pd.NaT, grouped_df['stock_time'])
# format the stock_time column
grouped_df['stock_time'] = pd.to_datetime(grouped_df['stock_time'])
grouped_df = grouped_df.sort_values(by='datetime')
# Backfill the stock_time2 column
grouped_df['stock_time'] = grouped_df['stock_time'].ffill().bfill()

In [20]:
# The choice of window here ultimately affects how much after-hours time should be counted towards market open
# For example, a 4-period window would mean that articles from 8:15 to 9:15 are counted towards the 9:30 period
windows = [4, 16, 48, 96]

for i in [j for j in grouped_df.columns if j not in ['datetime', 'date', 'time', 'stock_time']]:
    for window in windows:
        grouped_df[f'{i}_cum{window:02d}'] = grouped_df[f'{i}'].rolling(window, min_periods=1).sum()

In [21]:
# Now we keep the last of each stock time to remove duplicate values.
grouped_df = grouped_df.drop_duplicates(subset=['stock_time'], keep='last')
grouped_df.index = grouped_df['stock_time']
grouped_df.sort_index(inplace=True)
grouped_df.drop(columns=['stock_time','datetime','time','date'], inplace=True)

In [26]:
# Calculate lags
cols = [i for i in grouped_df.columns if 'cum' not in i]
for j in cols:
    for i in [1,2,4,16,26]:
        grouped_df[f'{j}_lag{i:02d}'] = grouped_df[f'{j}'].shift(i)


cols = [i for i in grouped_df.columns if 'cum' in i]
for j in cols:
    grouped_df[f'{j}_lag01'] = grouped_df[f'{j}'].shift(1)


In [27]:
grouped_df.shape

(48418, 25872)

In [28]:
# Keep only the lagged columns
grouped_df = grouped_df[[col for col in grouped_df.columns if 'lag' in col]]

In [29]:
grouped_df = grouped_df.dropna()
# Order the columns alphabetically
grouped_df = grouped_df.reindex(sorted(grouped_df.columns), axis=1)

In [30]:
pd.to_pickle(grouped_df, '../../data/processed/temp_save.pkl')

In [3]:
grouped_df = pd.read_pickle('../../data/processed/temp_save.pkl')

In [ ]:
# Split columns into MultiIndex (ticker, metric)
grouped_df.columns = grouped_df.columns.str.split('_', n=1, expand=True)
grouped_df = grouped_df.stack(level=0).rename_axis(['date', 'ticker']).reset_index()
grouped_df = grouped_df.set_index(['date', 'ticker'])

Article Count_cum04_lag01  \
date                ticker                              
2018-01-03 09:45:00 AAL                           4.0   
                    ALGT                          0.0   
                    ALK                          10.0   
                    DAL                           3.0   
                    JBLU                          2.0   
...                                               ...   
2025-05-30 15:45:00 ALK                           0.0   
                    DAL                           3.0   
                    JBLU                          1.0   
                    LUV                           2.0   
                    UAL                           5.0   

                            Article Count_cum16_lag01  \
date                ticker                              
2018-01-03 09:45:00 AAL                          25.0   
                    ALGT                          0.0   
                    ALK                          24.0   
                    DAL                           7.0   
                    JBLU                          9.0   
...                                               ...   
2025-05-30 15:45:00 ALK                           3.0   
                    DAL                          12.0   
                    JBLU                          4.0   
                    LUV                           3.0   
                    UAL                          20.0   

                            Article Count_cum48_lag01  \
date                ticker                              
2018-01-03 09:45:00 AAL                          80.0   
                    ALGT                          2.0   
                    ALK                         185.0   
                    DAL                          24.0   
                    JBLU                         17.0   
...                                               ...   
2025-05-30 15:45:00 ALK                           9.0   
                    DAL                          15.0   
                    JBLU                         13.0   
                    LUV                          11.0   
                    UAL                          41.0   

                            Article Count_cum96_lag01  Article Count_lag01  \
date                ticker                                                   
2018-01-03 09:45:00 AAL                         143.0                  2.0   
                    ALGT                          2.0                  0.0   
                    ALK                         241.0                  0.0   
                    DAL                          52.0                  0.0   
                    JBLU                         40.0                  0.0   
...                                               ...                  ...   
2025-05-30 15:45:00 ALK                          31.0                  0.0   
                    DAL                          43.0                  0.0   
                    JBLU                         49.0                  0.0   
                    LUV                          30.0                  1.0   
                    UAL                         107.0                  0.0   

                            Article Count_lag02  Article Count_lag04  \
date                ticker                                             
2018-01-03 09:45:00 AAL                     1.0                  2.0   
                    ALGT                    0.0                  0.0   
                    ALK                     5.0                  0.0   
                    DAL                     1.0                  0.0   
                    JBLU                    1.0                  0.0   
...                                         ...                  ...   
2025-05-30 15:45:00 ALK                     0.0                  0.0   
                    DAL                     1.0                  1.0   
                    JBLU                    0.0                  0.

In [5]:
grouped_df = downcast(grouped_df, verbose = True)
grouped_df

49.8% compressed


Article Count_cum04_lag01  \
date                ticker                              
2018-01-03 09:45:00 AAL                             4   
                    ALGT                            0   
                    ALK                            10   
                    DAL                             3   
                    JBLU                            2   
...                                               ...   
2025-05-30 15:45:00 ALK                             0   
                    DAL                             3   
                    JBLU                            1   
                    LUV                             2   
                    UAL                             5   

                            Article Count_cum16_lag01  \
date                ticker                              
2018-01-03 09:45:00 AAL                            25   
                    ALGT                            0   
                    ALK                            24   
                    DAL                             7   
                    JBLU                            9   
...                                               ...   
2025-05-30 15:45:00 ALK                             3   
                    DAL                            12   
                    JBLU                            4   
                    LUV                             3   
                    UAL                            20   

                            Article Count_cum48_lag01  \
date                ticker                              
2018-01-03 09:45:00 AAL                            80   
                    ALGT                            2   
                    ALK                           185   
                    DAL                            24   
                    JBLU                           17   
...                                               ...   
2025-05-30 15:45:00 ALK                             9   
                    DAL                            15   
                    JBLU                           13   
                    LUV                            11   
                    UAL                            41   

                            Article Count_cum96_lag01  Article Count_lag01  \
date                ticker                                                   
2018-01-03 09:45:00 AAL                           143                    2   
                    ALGT                            2                    0   
                    ALK                           241                    0   
                    DAL                            52                    0   
                    JBLU                           40                    0   
...                                               ...                  ...   
2025-05-30 15:45:00 ALK                            31                    0   
                    DAL                            43                    0   
                    JBLU                           49                    0   
                    LUV                            30                    1   
                    UAL                           107                    0   

                            Article Count_lag02  Article Count_lag04  \
date                ticker                                             
2018-01-03 09:45:00 AAL                       1                    2   
                    ALGT                      0                    0   
                    ALK                       5                    0   
                    DAL                       1                    0   
                    JBLU                      1                    0   
...                                         ...                  ...   
2025-05-30 15:45:00 ALK                       0                    0   
                    DAL                       1                    1   
                    JBLU                      0                    

In [8]:
index = grouped_df.index
df = grouped_df.copy()

for metric in ['llm', 'sentiment']:
    cols_to_pca = [i for i in df.columns if metric in i]
    df_to_pca = df[cols_to_pca]
    scaler = StandardScaler()
    df_to_pca = scaler.fit_transform(df_to_pca)
    pca = PCA()
    df_to_pca = pca.fit_transform(df_to_pca)
    cum_var = np.cumsum(pca.explained_variance_ratio_)
    n_components = np.argmax(cum_var >= 0.8) + 1
    
    df_to_pca = pd.DataFrame(df_to_pca[:,:n_components], index=index, columns=[f'{metric}_pca_{i+1:03d}' for i in range(n_components)])
    df.drop(columns=cols_to_pca, inplace=True)
    df = pd.concat([df, df_to_pca], axis=1)

df.shape

(338744, 634)

In [11]:
df['date'] = df.index.get_level_values('date')
df['ticker'] = df.index.get_level_values('ticker')

In [13]:
# Export to pickle object
with open(r"../../Data/Processed/GDELT_Clean_202507141200.pkl", 'wb') as f:
    pickle.dump(df, f)